## 4.6　集計処理

### 4.6.1　グループ集計

In [1]:
import pandas as pd         # pandasをpdの名で読込み
from scipy import stats     # scipy.statsの読込み
import numpy as np          # NumPyのnpの名で読込み

In [2]:
# テストデータの作成
rA = stats.norm.rvs( loc=-3, scale=3,   size=10000, random_state=1 )  # μ=-3, σ=3
rB = stats.norm.rvs( loc=0,  scale=1,   size=10000, random_state=2 )  # μ=0,  σ=1
rC = stats.norm.rvs( loc=1,  scale=0.5, size=10000, random_state=3 )  # μ=1,  σ=0.5

In [3]:
# DataFrameにする
df = pd.DataFrame(None,columns=['種類','値'])
df['種類'] = ['A']*len(rA) + ['B']*len(rB) + ['C']*len(rC)
df['値'] = np.concatenate([rA,rB,rC])
# シャッフルする
dfR = df.sample(frac=1,random_state=4).reset_index(drop=True)
dfR.head(4)

種類         値
0  A -4.392193
1  A -4.406021
2  B -1.907950
3  C  0.697232

In [4]:
print( '平均:', dfR['値'].mean() )
print( '標準偏差:', dfR['値'].std() )

平均: -0.667900972250482
標準偏差: 2.4958058728041013


In [5]:
g = dfR.groupby('種類')   # グループ化処理
print( type(g) )
display(  g.mean() )
display( g.std() )

<class 'pandas.core.groupby.generic.DataFrameGroupBy'>


値
種類          
A  -2.970682
B  -0.019192
C   0.986171

値
種類          
A   2.996507
B   1.000467
C   0.497968

In [6]:
g.describe()

値                                                               \
      count      mean       std        min       25%       50%       75%   
種類                                                                         
A   10000.0 -2.970682  2.996507 -13.969320 -4.988775 -2.974638 -0.984573   
B   10000.0 -0.019192  1.000467  -3.582359 -0.688269 -0.020273  0.641505   
C   10000.0  0.986171  0.497968  -0.874970  0.650109  0.985504  1.323182   

              
         max  
種類            
A   9.080547  
B   4.133362  
C   3.045696

### 4.6.2　クロス集計

In [7]:
dtab = pd.DataFrame(columns=['出身地','年齢','好物'])  # データフレームの作成

In [8]:
import random     # リストのシャッフルに使用するモジュールの読込み
p = ['大阪','京都','東京']*100
m = ['お好み焼き']*80 + ['カレーライス']*120 + ['おでん']*50 + ['肉うどん']*50
random.seed(1)
random.shuffle(p)       # '出身地' の列をシャッフル
random.seed(2)
random.shuffle(m)       # '好物' の列をシャッフル
dtab['出身地'] = p
dtab['好物']  = m
# 年齢には適当に乱数を設定
dtab['年齢'] = stats.norm.rvs(loc=35,scale=10,size=300,random_state=5).astype('uint32')
dtab.head(5)

出身地  年齢      好物
0  東京  39  カレーライス
1  大阪  31     おでん
2  京都  59  カレーライス
3  京都  32     おでん
4  大阪  36    肉うどん

#### 4.6.2.1 crosstab

In [9]:
ct = pd.crosstab( dtab['出身地'], dtab['好物'] )
ct

好物   おでん  お好み焼き  カレーライス  肉うどん
出身地                          
京都    15     27      43    15
大阪    21     25      41    13
東京    14     28      36    22

In [10]:
ct = pd.crosstab( dtab['出身地'], dtab['好物'], margins=True )
ct

好物   おでん  お好み焼き  カレーライス  肉うどん  All
出身地                               
京都    15     27      43    15  100
大阪    21     25      41    13  100
東京    14     28      36    22  100
All   50     80     120    50  300

#### 4.6.2.2 pivot_table

In [11]:
pt = dtab.pivot_table(index='出身地',columns='好物',values='年齢',
                      aggfunc='mean', margins=True)
pt

好物         おでん      お好み焼き     カレーライス       肉うどん    All
出身地                                                   
京都   33.866667  34.481481  37.534884  30.333333  35.08
大阪   37.809524  35.160000  33.048780  33.461538  34.63
東京   34.071429  33.642857  35.083333  31.545455  33.76
All  35.580000  34.400000  35.266667  31.680000  34.49

In [12]:
pt = dtab.pivot_table(index='出身地',columns='好物',values='年齢',
                      aggfunc='max',margins=True)
pt

好物   おでん  お好み焼き  カレーライス  肉うどん  All
出身地                               
京都    56     50      60    42   60
大阪    57     57      55    49   57
東京    50     49      48    52   52
All   57     57      60    52   60

In [13]:
pt = dtab.pivot_table(index='出身地',columns='好物',values='年齢',
                      aggfunc='count',margins=True)
pt

好物   おでん  お好み焼き  カレーライス  肉うどん  All
出身地                               
京都    15     27      43    15  100
大阪    21     25      41    13  100
東京    14     28      36    22  100
All   50     80     120    50  300

### 4.6.3 ダミー変数の取得（ワンホットエンコーディング）

In [14]:
# サンプルデータ
d = pd.DataFrame(columns=['氏名','出身地'])
d['氏名']   = ['中村 勝則','田中 由恵','平田 洋子']
d['出身地'] = ['大阪府','京都府','東京都']
display(d)

氏名  出身地
0  中村 勝則  大阪府
1  田中 由恵  京都府
2  平田 洋子  東京都

In [15]:
dmy = pd.get_dummies(d,columns=['出身地'])
display(dmy)

氏名  出身地_京都府  出身地_大阪府  出身地_東京都
0  中村 勝則        0        1        0
1  田中 由恵        1        0        0
2  平田 洋子        0        0        1

In [16]:
dmy = pd.get_dummies(d)
display(dmy)

氏名_中村 勝則  氏名_平田 洋子  氏名_田中 由恵  出身地_京都府  出身地_大阪府  出身地_東京都
0         1         0         0        0        1        0
1         0         0         1        1        0        0
2         0         1         0        0        0        1